# Capstone Final Project - Battle of the Neighborhoods 
# New Orleans Food Truck Location

In [1]:
#import libraries
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import numpy as np
import requests 
from bs4 import BeautifulSoup 


import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values


!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')


Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.21.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

In [2]:
# Use the Notebook to build the code to scrape the following Wikipedia page,
#https://en.wikipedia.org/wiki/List_of_neighborhoods_in_Miami, in order to obtain 
#the data that is in the table of neighborhoods and to transform the data into a pandas dataframe
req = requests.get("https://en.wikipedia.org/wiki/Neighborhoods_in_New_Orleans") 
soup = BeautifulSoup(req.content,'lxml') 
table = soup.find_all('table')[0] 
df = pd.read_html(str(table)) 

nola=pd.DataFrame(df[0]) 
nola.head(5)

Neighborhood  Longitude   Latitude
0  U.S. NAVAL BASE -90.026093  29.946085
1    ALGIERS POINT -90.051606  29.952462
2          WHITNEY -90.042357  29.947200
3          AUDUBON -90.121450  29.932994
4       OLD AURORA -90.000000  29.924440

In [3]:
nola.dtypes

Neighborhood     object
Longitude       float64
Latitude        float64
dtype: object

In [4]:
#Dropping the rows with missing data for coordinates
nola.dropna(subset=['Longitude'], inplace=True)

In [5]:
nola['Latitude'] = pd.to_numeric(nola['Latitude'], errors='coerce')
nola['Longitude'] = pd.to_numeric(nola['Longitude'], errors='coerce')

In [6]:
#Identifying coordinates without corresponding neighborhood
blank_hood = nola[nola['Neighborhood'].isna()].shape[0]
print('Number of rows with missing Neighborhood: {}'.format(blank_hood))

Number of rows with missing Neighborhood: 0


In [7]:
print('The shape of the dataset is:',nola.shape)

The shape of the dataset is: (72, 3)


In [8]:
# Getting the Latitude and Longitude of Miami city
address = 'New Orleans, LA'

geolocator = Nominatim(user_agent="mi_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinates of New Orleans are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of New Orleans are 29.9499323, -90.0701156.


In [9]:
# Creating a map of the neighborhoods in the city of New Orleans
map_nola = folium.Map(location=[latitude, longitude], zoom_start=12)

# adding markers to map
for lat, lng, neighborhood in zip (nola['Latitude'], 
                                  nola['Longitude'], 
                                  nola['Neighborhood']):
  
 folium.CircleMarker(
        [lat, lng],
        radius=5,
        fill_opacity=0.7).add_to(map_nola)  
    
map_nola

In [10]:
# Exploring venues of Miami using Four Square API
CLIENT_ID = '' # Foursquare ID
CLIENT_SECRET = '' # Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('My credentails:')
print('CLIENT_ID:')
print('CLIENT_SECRET:')


My credentails:
CLIENT_ID:
CLIENT_SECRET:


In [11]:
# Exploring the latitude and longitude of a certain neighborhood of Miami 
N_latitude = nola.loc[22, 'Latitude'] # Neighborhood latitude value
N_longitude = nola.loc[22, 'Longitude'] # Neighborhood longitude value

N_name = nola.loc[3, 'Neighborhood'] # Neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(N_name, 
                                                               N_latitude, 
                                                               N_longitude))

Latitude and longitude values of AUDUBON are 29.93239931, -90.04154205.


In [12]:
# setting up result limit and defining radius
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 1000 # define radius

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    N_latitude, 
    N_longitude, 
    radius, 
    LIMIT)
url

results = requests.get(url).json() # make the GET request

In [13]:
# function for finding the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [14]:
# Finding the venues of the neighborhood and cleaning the Json file
venues = results['response']['groups'][0]['items']
nearby_venues = json_normalize(venues) # flattening JSON

# filtering columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1) # filtering the category for each row

nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns] # Preparing columns

nearby_venues.head(10)

name         categories        lat  \
0    Courtyard New Orleans Westbank/Gretna              Hotel  29.925624   
1  Holiday Inn New Orleans West Bank Tower              Hotel  29.924540   
2                        Franklin Discount  Convenience Store  29.928978   
3                      Algiers Flea Market        Flea Market  29.928227   
4                Homewood Suites by Hilton              Hotel  29.926705   
5         Seersucker Restaurant & Catering     Sandwich Place  29.929609   
6                                     IHOP     Breakfast Spot  29.924937   
7                                  entergy  Electronics Store  29.927411   
8                                   Avenue      Women's Store  29.925710   
9               Braxton Restaurant& Lounge         Restaurant  29.932854   

         lng  
0 -90.041487  
1 -90.041757  
2 -90.049343  
3 -90.037796  
4 -90.041440  
5 -90.048205  
6 -90.039805  
7 -90.046462  
8 -90.042030  
9 -90.049635

In [15]:
# Number of venues returned by Foursquare
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

12 venues were returned by Foursquare.


In [16]:
## Exploring the Neighborhoods of Miami; Getting venues for all neighborhoods of Miami
def getNearbyVenues(names, latitudes, longitudes, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [17]:

nola_venues = getNearbyVenues(names=nola['Neighborhood'],
                                latitudes=nola['Latitude'],
                                longitudes=nola['Longitude'])

U.S. NAVAL BASE
ALGIERS POINT
WHITNEY
AUDUBON
OLD AURORA
B. W. COOPER
BAYOU ST. JOHN
BEHRMAN
BLACK PEARL
BROADMOOR
MARLYVILLE - FONTAINEBLEAU
GERT TOWN
MID-CITY
ST. CLAUDE
CENTRAL BUSINESS DISTRICT
FRENCH QUARTER
CENTRAL CITY
LAKE CATHERINE
VILLAGE DE LEST
VIAVANT - VENETIAN ISLES
NEW AURORA - ENGLISH TURN
TALL TIMBERS - BRECHTEL
FISCHER DEV
McDONOGH
LOWER GARDEN DISTRICT
ST. THOMAS DEV
EAST RIVERSIDE
IRISH CHANNEL
TOURO
MILAN
UPTOWN
WEST RIVERSIDE
EAST CARROLLTON
FRERET
GARDEN DISTRICT
LEONIDAS
HOLLYGROVE
TULANE - GRAVIER
TREME - LAFITTE
SEVENTH WARD
MARIGNY
ST. ROCH
DIXON
LAKEWOOD
NAVARRE
CITY PARK
LAKEVIEW
WEST END
LAKESHORE - LAKE VISTA
FILMORE
ST. BERNARD AREA
DILLARD
ST. ANTHONY
LAKE TERRACE & OAKS
MILNEBURG
PONTCHARTRAIN PARK
GENTILLY WOODS
GENTILLY TERRACE
DESIRE AREA
FLORIDA AREA
FLORIDA DEV
LOWER NINTH WARD
BYWATER
HOLY CROSS
PINES VILLAGE
PLUM ORCHARD
READ BLVD WEST
READ BLVD EAST
WEST LAKE FOREST
LITTLE WOODS
FAIRGROUNDS
IBERVILLE


In [18]:
# Size of dataframe
nola_venues.shape

(2725, 7)

In [19]:
#Number of venues per neighborhood in New Orleans
nola_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                
ALGIERS POINT                                  23                      23   
AUDUBON                                        33                      33   
B. W. COOPER                                   30                      30   
BAYOU ST. JOHN                                 72                      72   
BEHRMAN                                        17                      17   
BLACK PEARL                                    61                      61   
BROADMOOR                                      59                      59   
BYWATER                                        37                      37   
CENTRAL BUSINESS DISTRICT                     100                     100   
CENTRAL CITY                                   48                      48   
CITY PARK                                      21                      21   
DESIRE AREA                                     2                       2   
DILLARD                                        14                      14   
DIXON                                          37                      37   
EAST CARROLLTON                                96                      96   
EAST RIVERSIDE                                 92                      92   
FAIRGROUNDS                                    47                      47   
FILMORE                                        13                      13   
FISCHER DEV                                    12                      12   
FLORIDA AREA                                    6                       6   
FLORIDA DEV                                     4                       4   
FRENCH QUARTER                                100                     100   
FRERET                                         53                      53   
GARDEN DISTRICT                               100                     100   
GENTILLY TERRACE                               18                      18   
GENTILLY WOODS                                 23                      23   
GERT TOWN                                      56                      56   
HOLLYGROVE                                     18                      18   
HOLY CROSS                                      8                       8   
IBERVILLE                                     100                     100   
IRISH CHANNEL                                  33                      33   
LAKE CATHERINE                                  1                       1   
LAKE TERRACE & OAKS                            18                      18   
LAKESHORE - LAKE VISTA                          9                       9   
LAKEVIEW                                       35                      35   
LAKEWOOD                                       19                      19   
LEONIDAS                                       47                      47   
LITTLE WOODS                                    8                       8   
LOWER GARDEN DISTRICT                         100                     100   
LOWER NINTH WARD                                9                       9   
MARIGNY                                       100                     100   
MARLYVILLE - FONTAINEBLEAU                     43                      43   
MID-CITY                                      100                     100   
MILAN                                          70                      70   
MILNEBURG                                      25                      25   
McDONOGH                                       16                      16   
NAVARRE                                        32                      32   
NEW AURORA - ENGLISH TURN                       5                       5   
OLD AURORA                                      7                       7   
PINES VILLAGE                                   9                       9   
PLUM ORCHARD            

In [20]:
#finding the list of categories
nola_venues['Venue Category'].unique()[:150]

array(['Stadium', 'Hotel', 'Sandwich Place', 'Boat or Ferry',
       'Construction & Landscaping', 'Credit Union', 'Basketball Court',
       'Auto Garage', 'Restaurant', 'Café', 'Bar', 'Coffee Shop',
       'Scenic Lookout', 'Music Venue', 'Pizza Place',
       'Seafood Restaurant', 'Arts & Crafts Store', 'Food & Drink Shop',
       'Park', 'New American Restaurant', 'Gift Shop', 'Neighborhood',
       'Food Truck', 'Bed & Breakfast', 'Spa', 'Recording Studio',
       'Intersection', 'Grocery Store', 'Plaza', 'Outdoors & Recreation',
       'College Arts Building', 'French Restaurant', 'Record Shop',
       'College Auditorium', 'Smoothie Shop', 'Art Gallery',
       'Clothing Store', 'Shipping Store', 'Track', 'Light Rail Station',
       'Soccer Field', 'Wine Bar', 'Snack Place', 'Gym', 'Ice Cream Shop',
       'General Travel', 'Pool', 'Donut Shop', 'American Restaurant',
       'Rental Car Location', 'Kitchen Supply Store', 'Brewery',
       'Basketball Stadium', 'Bakery', 'Wings 

In [21]:
# Exploring the results containing the word "Food Truck"
"Food Truck" in nola_venues['Venue Category'].unique()

True

In [22]:
## Analzing Each Neighborhood - one hot encoding
nola_onehot = pd.get_dummies(nola_venues[['Venue Category']], prefix="", prefix_sep="")

# adding neighborhood column to dataframe
nola_onehot['Neighborhood'] = nola_venues['Neighborhood'] 

# moving neighborhood column to the first column
fixed_columns = [nola_onehot.columns[-1]] + list(nola_onehot.columns[:-1])
nola_onehot = nola_onehot[fixed_columns]


nola_onehot.head (5)

Yoga Studio  Accessories Store  American Restaurant  Antique Shop  \
0            0                  0                    0             0   
1            0                  0                    0             0   
2            0                  0                    0             0   
3            0                  0                    0             0   
4            0                  0                    0             0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Automotive Shop  \
0                 0                   0            0                0   
1                 0                   0            0                0   
2                 0                   0            0                0   
3                 0                   0            0                0   
4                 0                   0            0                0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0                   0      0                0         0            0   
1                   0      0                0         0            0   
2                   0      0                0         0            0   
3                   0      0                0         0            0   
4                   0      0                0         0            0   

   Beer Store  Big Box Store  Bike Rental / Bike Share  Bike Trail  Bistro  \
0           0              0                         0           0       0   
1           0              0                         0           0       0   
2           0              0                         0           0       0   
3           0              0                         0           0       0   
4           0              0                         0           0       0   

   Boat or Ferry  Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  \
0              0          0         0              0                     0   
1              0          0         0              0                     0   
2              0          0         0              0                     0   
3              1          0         0              0                     0   
4              1          0         0              0                     0   

   Breakfast Spot  Brewery  Burger Joint  Burrito Place  Bus Station  \
0               0        0             0              0            0   
1               0        0             0              0            0   
2               0        0             0              0            0   
3               0        0             0              0            0   
4               0        0             0              0            0   

   Bus Stop  Business Service  Butcher  Café  Cajun / Creole Restaurant  \
0         0                 0        0     0                          0   
1         0                 0        0     0                          0   
2         0                 0        0     0                          0   
3         0                 0        0     0                          0   
4         0   

In [23]:
#group rows by neighborhood and get the mean of the frequency of occurrence of each category
nola_grouped = nola_onehot.groupby(["Neighborhood"]).mean().reset_index()

print(nola_grouped.shape)
nola_grouped

(70, 272)


Neighborhood  Yoga Studio  Accessories Store  \
0                ALGIERS POINT     0.000000           0.000000   
1                      AUDUBON     0.000000           0.000000   
2                 B. W. COOPER     0.000000           0.000000   
3               BAYOU ST. JOHN     0.000000           0.000000   
4                      BEHRMAN     0.000000           0.000000   
5                  BLACK PEARL     0.000000           0.000000   
6                    BROADMOOR     0.000000           0.000000   
7                      BYWATER     0.000000           0.000000   
8    CENTRAL BUSINESS DISTRICT     0.000000           0.010000   
9                 CENTRAL CITY     0.000000           0.000000   
10                   CITY PARK     0.000000           0.000000   
11                 DESIRE AREA     0.000000           0.000000   
12                     DILLARD     0.000000           0.000000   
13                       DIXON     0.000000           0.000000   
14             EAST CARROLLTON     0.010417           0.000000   
15              EAST RIVERSIDE     0.021739           0.000000   
16                 FAIRGROUNDS     0.000000           0.000000   
17                     FILMORE     0.000000           0.000000   
18                 FISCHER DEV     0.000000           0.000000   
19                FLORIDA AREA     0.000000           0.000000   
20                 FLORIDA DEV     0.000000           0.000000   
21              FRENCH QUARTER     0.000000           0.040000   
22                      FRERET     0.018868           0.000000   
23             GARDEN DISTRICT     0.010000           0.020000   
24            GENTILLY TERRACE     0.000000           0.000000   
25              GENTILLY WOODS     0.000000           0.000000   
26                   GERT TOWN     0.000000           0.000000   
27                  HOLLYGROVE     0.000000           0.000000   
28                  HOLY CROSS     0.000000           0.000000   
29                   IBERVILLE     0.000000           0.000000   
30               IRISH CHANNEL     0.000000           0.000000   
31              LAKE CATHERINE     0.000000           0.000000   
32         LAKE TERRACE & OAKS     0.000000           0.000000   
33      LAKESHORE - LAKE VISTA     0.000000           0.000000   
34                    LAKEVIEW     0.000000           0.000000   
35                    LAKEWOOD     0.000000           0.000000   
36                    LEONIDAS     0.021277           0.000000   
37                LITTLE WOODS     0.000000           0.000000   
38       LOWER GARDEN DISTRICT     0.000000           0.010000   
39            LOWER NINTH WARD     0.000000           0.000000   
40                     MARIGNY     0.010000           0.000000   
41  MARLYVILLE - FONTAINEBLEAU     0.000000           0.000000   
42                    MID-CITY     0.010000           0.000000   
43                       MILAN     0.014286           0.000000   
44                   MILNEBURG     0.000000           0.000000   
45                    McDONOGH     0.000000           0.000000   
46                     NAVARRE     0.000000           0.000000   
47   NEW AURORA - ENGLISH TURN     0.000000           0.000000   
48                  OLD AURORA     0.000000           0.000000   
49               PINES VILLAGE     0.000000           0.000000   
50                PLUM ORCHARD     0.000000           0.000000   
51          PONTCHARTRAIN PARK     0.000000           0.000000   
52              READ BLVD EAST     0.000000           0.000000   
53              READ BLVD WEST     0.000000           0.000000   
54                SEVENTH WARD     0.021739           0.000000   
55                 ST. ANTHONY     0.000000           0.000000   
56            ST. BERNARD AREA     0.000000           0.000000   
57                  ST. CLAUDE     0.000000           0.000000   
58                    ST. ROCH     0.000000           0.000000   
59              ST. THOMAS DEV     0.000000           0.02

In [24]:
#number of neighborhoods where Food Truck is > 0
len(nola_grouped[nola_grouped["Food Truck"] > 0])

14

In [26]:
nola2_grouped = nola_grouped[["Neighborhood","Food Truck"]]
nola2_grouped.head(72)

Neighborhood  Food Truck
0                ALGIERS POINT    0.043478
1                      AUDUBON    0.000000
2                 B. W. COOPER    0.033333
3               BAYOU ST. JOHN    0.013889
4                      BEHRMAN    0.000000
5                  BLACK PEARL    0.016393
6                    BROADMOOR    0.000000
7                      BYWATER    0.000000
8    CENTRAL BUSINESS DISTRICT    0.010000
9                 CENTRAL CITY    0.000000
10                   CITY PARK    0.000000
11                 DESIRE AREA    0.000000
12                     DILLARD    0.000000
13                       DIXON    0.000000
14             EAST CARROLLTON    0.000000
15              EAST RIVERSIDE    0.032609
16                 FAIRGROUNDS    0.000000
17                     FILMORE    0.000000
18                 FISCHER DEV    0.000000
19                FLORIDA AREA    0.000000
20                 FLORIDA DEV    0.000000
21              FRENCH QUARTER    0.000000
22                      FRERET    0.000000
23             GARDEN DISTRICT    0.010000
24            GENTILLY TERRACE    0.000000
25              GENTILLY WOODS    0.000000
26                   GERT TOWN    0.000000
27                  HOLLYGROVE    0.000000
28                  HOLY CROSS    0.000000
29                   IBERVILLE    0.020000
30               IRISH CHANNEL    0.030303
31              LAKE CATHERINE    0.000000
32         LAKE TERRACE & OAKS    0.000000
33      LAKESHORE - LAKE VISTA    0.000000
34                    LAKEVIEW    0.000000
35                    LAKEWOOD    0.000000
36                    LEONIDAS    0.000000
37                LITTLE WOODS    0.000000
38       LOWER GARDEN DISTRICT    0.000000
39            LOWER NINTH WARD    0.000000
40                     MARIGNY    0.000000
41  MARLYVILLE - FONTAINEBLEAU    0.000000
42                    MID-CITY    0.000000
43                       MILAN    0.000000
44                   MILNEBURG    0.000000
45                    McDONOGH    0.000000
46                     NAVARRE    0.000000
47   NEW AURORA - ENGLISH TURN    0.000000
48                  OLD AURORA    0.000000
49               PINES VILLAGE    0.000000
50                PLUM ORCHARD    0.000000
51          PONTCHARTRAIN PARK    0.000000
52              READ BLVD EAST    0.000000
53              READ BLVD WEST    0.000000
54                SEVENTH WARD    0.000000
55                 ST. ANTHONY    0.000000
56            ST. BERNARD AREA    0.000000
57                  ST. CLAUDE    0.000000
58                    ST. ROCH    0.000000
59              ST. THOMAS DEV    0.012821
60     TALL TIMBERS - BRECHTEL    0.000000
61                       TOURO    0.020000
62             TREME - LAFITTE    0.013889
63            TULANE - GRAVIER    0.020000
64             U.S. NAVAL BASE    0.000000
65                      UPTOWN    0.000000
66                    WEST END    0.000000
67            WEST LAKE FOREST    0.076923
68              WEST RIVERSIDE    0.000000
69                     WHITNEY    0.000000

# K-Means Clustering

In [27]:
# set number of clusters
toclusters = 5

to_clustering = nola2_grouped.drop(["Neighborhood"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 0, 3, 4, 0, 2, 0, 0, 4, 0], dtype=int32)

In [28]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
Cluster = nola2_grouped.copy()

# add clustering labels
Cluster["Cluster Labels"] = kmeans.labels_

Cluster.rename(columns={"Neighborhood": "Neighborhood"}, inplace=True)
Cluster.head(72)

Neighborhood  Food Truck  Cluster Labels
0                ALGIERS POINT    0.043478               3
1                      AUDUBON    0.000000               0
2                 B. W. COOPER    0.033333               3
3               BAYOU ST. JOHN    0.013889               4
4                      BEHRMAN    0.000000               0
5                  BLACK PEARL    0.016393               2
6                    BROADMOOR    0.000000               0
7                      BYWATER    0.000000               0
8    CENTRAL BUSINESS DISTRICT    0.010000               4
9                 CENTRAL CITY    0.000000               0
10                   CITY PARK    0.000000               0
11                 DESIRE AREA    0.000000               0
12                     DILLARD    0.000000               0
13                       DIXON    0.000000               0
14             EAST CARROLLTON    0.000000               0
15              EAST RIVERSIDE    0.032609               3
16                 FAIRGROUNDS    0.000000               0
17                     FILMORE    0.000000               0
18                 FISCHER DEV    0.000000               0
19                FLORIDA AREA    0.000000               0
20                 FLORIDA DEV    0.000000               0
21              FRENCH QUARTER    0.000000               0
22                      FRERET    0.000000               0
23             GARDEN DISTRICT    0.010000               4
24            GENTILLY TERRACE    0.000000               0
25              GENTILLY WOODS    0.000000               0
26                   GERT TOWN    0.000000               0
27                  HOLLYGROVE    0.000000               0
28                  HOLY CROSS    0.000000               0
29                   IBERVILLE    0.020000               2
30               IRISH CHANNEL    0.030303               3
31              LAKE CATHERINE    0.000000               0
32         LAKE TERRACE & OAKS    0.000000               0
33      LAKESHORE - LAKE VISTA    0.000000               0
34                    LAKEVIEW    0.000000               0
35                    LAKEWOOD    0.000000               0
36                    LEONIDAS    0.000000               0
37                LITTLE WOODS    0.000000               0
38       LOWER GARDEN DISTRICT    0.000000               0
39            LOWER NINTH WARD    0.000000               0
40                     MARIGNY    0.000000               0
41  MARLYVILLE - FONTAINEBLEAU    0.000000               0
42                    MID-CITY    0.000000               0
43                       MILAN    0.000000               0
44                   MILNEBURG    0.000000               0
45                    McDONOGH    0.000000               0
46                     NAVARRE    0.000000               0
47   NEW AURORA - ENGLISH TURN    0.000000               0
48                  OLD AURORA    0.000000               0
49               PINES VILLAGE    0.000000               0
50                PLUM ORCHARD    0.000000               0
51          PONTCHARTRAIN PARK    0.000000               0
52              READ BLVD EAST    0.000000               0
53              READ BLVD WEST    0.000000               0
54                SEVENTH WARD    0.000000               0
55                 ST. ANTHONY    0.000000               0
56            ST. BERNARD AREA    0.000000               0
57                  ST. CLAUDE    0.000000               0
58                    ST. ROCH    0.000000               0
59              ST. THOMAS DEV    0.012821               4
60     TALL TIMBERS - BRECHTEL    0.000000               0
61                       TOURO    0.020000               2
62             TREME - LAFITTE    0.013889               4
63            TULANE - GRAVIER    0.020000               2
64             U.S. NAVAL BASE    0.000000               0
65                      UPTOWN    0.000000               0
66                    WEST END    0.000000               0
67    

In [29]:
#merging nola_grouped with Cluster Labels data to add latitude/longitude for each neighborhood
Cluster = Cluster.join(nola_venues.set_index("Neighborhood"), on="Neighborhood")

print(Cluster.shape)
Cluster.head(5)

(2725, 9)


Neighborhood  Food Truck  Cluster Labels  Neighborhood Latitude  \
0  ALGIERS POINT    0.043478               3              29.952462   
0  ALGIERS POINT    0.043478               3              29.952462   
0  ALGIERS POINT    0.043478               3              29.952462   
0  ALGIERS POINT    0.043478               3              29.952462   
0  ALGIERS POINT    0.043478               3              29.952462   

   Neighborhood Longitude                         Venue  Venue Latitude  \
0              -90.051606            Tout de Suite Café       29.952121   
0              -90.051606            The Crown & Anchor       29.951416   
0              -90.051606                 Old Point Bar       29.954940   
0              -90.051606  Congregation Coffee Roasters       29.951918   
0              -90.051606         Levee @ Algiers Point       29.951760   

   Venue Longitude  Venue Category  
0       -90.051090            Café  
0       -90.054220             Bar  
0       -90.050226             Bar  
0       -90.053395     Coffee Shop  
0       -90.048747  Scenic Lookout

In [30]:
#sorting the output by Cluster Labels
print(Cluster.shape)
Cluster.sort_values(["Cluster Labels"], inplace=True)
Cluster.head()

(2725, 9)


Neighborhood  Food Truck  Cluster Labels  Neighborhood Latitude  \
34     LAKEVIEW         0.0               0              30.006605   
40      MARIGNY         0.0               0              29.965048   
40      MARIGNY         0.0               0              29.965048   
40      MARIGNY         0.0               0              29.965048   
40      MARIGNY         0.0               0              29.965048   

    Neighborhood Longitude                                     Venue  \
34              -90.108318                           Creole Creamery   
40              -90.055876                       Central Grocery Co.   
40              -90.055876                          The New Movement   
40              -90.055876                   Madame Isabelle's House   
40              -90.055876  Royal Street Courtyard Bed and Breakfast   

    Venue Latitude  Venue Longitude   Venue Category  
34       30.004026       -90.106955   Ice Cream Shop  
40       29.958837       -90.061055    Deli / Bodega  
40       29.966482       -90.059782      Comedy Club  
40       29.966229       -90.062083           Hostel  
40       29.964711       -90.053147  Bed & Breakfast

# Analysis of the Clusters

In [31]:
#create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11,tiles='cartodbpositron')

#set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

In [32]:
#add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Cluster['Neighborhood Latitude'], Cluster['Neighborhood Longitude'], Cluster['Neighborhood'], Cluster['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [55]:
#Cluster 0
Cluster.loc[Cluster['Cluster Labels'] == 0]

Neighborhood  Food Truck  Cluster Labels  \
0                ALGIERS POINT         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
40                     MARIGNY         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
40                     MARIGNY         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0               0   
41  MARLYVILLE - FONTAINEBLEAU         0.0        

In [56]:
#Cluster 1
Cluster.loc[Cluster['Cluster Labels'] == 1]

Neighborhood  Food Truck  Cluster Labels  Neighborhood Latitude  \
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   
67  WEST LAKE FOREST    0.076923               1              30.027043   

    Neighborhood Longitude                                             Venue  \
67              -89.992104                                            Subway   
67              -89.992104                          Liberty Bank New Orleans   
67              -89.992104                                     Family Dollar   
67              -89.992104                               Green Fleet Courier   
67              -89.992104                                    Planet Fitness   
67              -89.992104  Ma Momma's House of Cornbread, Chicken & Waffles   
67              -89.992104                                 Rodney's Snoballs   
67              -89.992104                                     daiquiri shop   
67              -89.992104                                  The Donut Bakery   
67              -89.992104                                Taqueria La Coyota   
67              -89.992104                                         Walgreens   
67              -89.992104                               Brother's Food Mart   
67              -89.992104                              Quality Inn & Suites   

    Venue Latitude  Venue Longitude       Venue Category  
67       30.028131       -89.992327       Sandwich Place  
67       30.034413       -89.996612                 Bank  
67       30.027000       -89.990500       Discount Store  
67       30.019756       -89.994347       Shipping Store  
67       30.027881       -89.994120                  Gym  
67       30.028050       -89.992013  American Restaurant  
67       30.029186       -89.983481          Snack Place  
67       30.028014       -89.992161               Lounge  
67       30.029220       -89.984164               Bakery  
67       30.030091       -89.993581           Food Truck  
67       30.027650       -89.993289             Pharmacy  
67       30.027715       -89.991655          Gas Station  
67       30.029281       -89.991795                Motel

In [57]:
#Cluster 2
Cluster.loc[Cluster['Cluster Labels'] == 2]

Neighborhood  Food Truck  Cluster Labels  Neighborhood Latitude  \
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOURO        0.02               2              29.923845   
61        TOU

In [58]:
#Cluster 3
Cluster.loc[Cluster['Cluster Labels'] == 3]

Neighborhood  Food Truck  Cluster Labels  Neighborhood Latitude  \
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.919605   
15  EAST RIVERSIDE    0.042553               3              29.9

In [59]:
#Cluster 4
Cluster.loc[Cluster['Cluster Labels'] == 4]

Neighborhood  Food Truck  Cluster Labels  \
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
8   CENTRAL BUSINESS DISTRICT    0.010000               4   
23            GARDEN DISTRICT    0.010000               4   
68             WEST RIVERSIDE    0.014493               4   
68             WEST RIVERSIDE    0.014493               4   
68             WEST RIVERSIDE    0.014493               4   
68             WEST RIVERSIDE    0.014493               4   
68             WEST RIVERSIDE    0.014493               4   
68             WEST RIVERSIDE    0.014493               4   
68             WEST RIVERSIDE    0.014493               4   
68             WEST RIVERSIDE    0.014493               4   
68             WEST RIVERSIDE    0.014493           